In [1]:
from haystack.document_stores.elasticsearch import ElasticsearchDocumentStore
from haystack.document_stores import FAISSDocumentStore
from haystack.nodes import TextConverter
from haystack.nodes import BM25Retriever
from haystack.nodes import EmbeddingRetriever
from haystack.nodes import FARMReader
from haystack.nodes import PreProcessor
from haystack.pipelines import ExtractiveQAPipeline
from haystack import Document
from haystack.utils import convert_files_to_docs
from pprint import  pprint
import logging

In [26]:
logging.basicConfig(format="%(levelname)s - %(name)s -  %(message)s", level=logging.WARNING)
logging.getLogger("haystack").setLevel(logging.INFO)

In [23]:
qa_dataset_path = "/home/eliran/Projects/wikipedia/data/squad20/"
wiki_train_filename = "dev-v2.0.json"

Create a reader win a pretrained model and train it on the new Squad dataset

In [3]:
#reader = FARMReader(model_name_or_path="distilbert-base-uncased-distilled-squad", use_gpu=True)

#reader.train(data_dir=qa_dataset_path, train_filename="dev-v2.0.json", use_gpu=True, n_epochs=1, save_dir="u2_squad_model")


In [4]:
#reader.save(directory="u2_squad_model")

In [2]:
import torch
torch.cuda.is_available()

True

In [4]:
import haystack 
haystack.__version__

'1.12.0rc0'

In [5]:
teacher = FARMReader(model_name_or_path="u2_squad_model", use_gpu=True)

/home/eliran/Projects/bin/haystack/haystack/modeling/model/language_model.py:865: ResourceWarning: unclosed file <_io.TextIOWrapper name='u2_squad_model/language_model_config.json' mode='r' encoding='UTF-8'>
  config = json.load(open(config_file))
/home/eliran/Projects/bin/haystack/haystack/modeling/model/prediction_head.py:108: ResourceWarning: unclosed file <_io.TextIOWrapper name='u2_squad_model/prediction_head_0_config.json' mode='r' encoding='UTF-8'>
  config = json.load(open(config_file))
/home/eliran/Projects/bin/haystack/haystack/modeling/data_handler/processor.py:174: ResourceWarning: unclosed file <_io.TextIOWrapper name='u2_squad_model/processor_config.json' mode='r' encoding='UTF-8'>
  config = json.load(open(processor_config_file))


In [6]:
student = FARMReader(model_name_or_path="huawei-noah/TinyBERT_General_6L_768D", use_gpu=True)

Some weights of the model checkpoint at huawei-noah/TinyBERT_General_6L_768D were not used when initializing BertForQuestionAnswering: ['cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'fit_denses.5.weight', 'fit_denses.4.weight', 'fit_denses.2.weight', 'fit_denses.6.bias', 'fit_denses.1.weight', 'fit_denses.3.bias', 'cls.predictions.transform.LayerNorm.weight', 'fit_denses.6.weight', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'fit_denses.5.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'fit_denses.0.weight', 'fit_denses.2.bias', 'fit_denses.0.bias', 'fit_denses.4.bias', 'fit_denses.3.weight', 'fit_denses.1.bias', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected 

In [5]:
!python distillary/augment_squad.py --squad_path ~/Projects/wikipedia/data/squad20/u2_wikipedia_squad.json --output_path distillary/augmented_dataset_2.json --multiplication_factor 20 --glove_path distillary/glove.42B.300d.txt 

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
100%|█████████████████████████████████████████████| 1/1 [00:25<00:00, 25.01s/it]


In [15]:
torch.cuda.empty_cache()

In [22]:
student.distil_intermediate_layers_from(teacher, 
    data_dir="/home/eliran/Projects/haystack/distillary/",
    save_dir="/home/eliran/Projects/haystack/student/",
    batch_size=10,
    caching=True,
    train_filename="augmented_dataset.json", 
    use_gpu=True)

Train epoch 4/4 (Cur. train loss: 0.3567): 100%|██████████| 8329/8329 [29:11<00:00,  4.76it/s]


In [25]:
student.distil_prediction_layer_from(teacher, 
    data_dir=qa_dataset_path, 
    train_filename=wiki_train_filename, 
    student_batch_size=10,
    use_gpu=True)

Train epoch 1/1 (Cur. train loss: 0.9138): 100%|██████████| 1360/1360 [03:33<00:00,  6.36it/s]


In [27]:
student.save(directory="wikipedia_u2_distilled_model")

INFO:haystack.nodes.reader.farm:Saving reader model to wikipedia_u2_distilled_model


In [18]:
torch.cuda.empty_cache() 

In [21]:
torch.cuda.memory_summary()

'|===========================================================================|\n|                  PyTorch CUDA memory summary, device ID 0                 |\n|---------------------------------------------------------------------------|\n|            CUDA OOMs: 4            |        cudaMalloc retries: 5         |\n|===========================================================================|\n|        Metric         | Cur Usage  | Peak Usage | Tot Alloc  | Tot Freed  |\n|---------------------------------------------------------------------------|\n| Allocated memory      |    1048 MB |   10662 MB |   20587 MB |   19539 MB |\n|       from large pool |    1039 MB |   10652 MB |   20104 MB |   19065 MB |\n|       from small pool |       9 MB |      10 MB |     483 MB |     473 MB |\n|---------------------------------------------------------------------------|\n| Active memory         |    1048 MB |   10662 MB |   20587 MB |   19539 MB |\n|       from large pool |    1039 MB |   10652 MB |

In [20]:
import gc
import torch
gc.collect()
torch.cuda.empty_cache()